### NetworkX, Matplotlib Animation Visualization

- first draft, still a lot of things are hardcoded into the update function
    - specific intersections and roads, which ones are the sinks, etc.
- prefer to integrate it so one could just pass in the `Map` object and it would instantiate the proper NetworkX graph
    - currently hardcoded in
    - difficulty because networkx positions are based on the nodes, but we have road LENGTHS
- Would like to make the color map better
    - min and max doesnt work, needs to be standardized across time, thinking of making some constants that the car densities will not exceed with high probability
    - or just make the maximum equivalent to the gridlock condition

In [23]:
import matplotlib.pyplot as plt
import matplotlib.cm as cm
from matplotlib.animation import FuncAnimation
from IPython.display import HTML
import numpy as np
import networkx as nx

from MODULE_simple_sim import *

In [24]:
# Initialize Map object, initialize roads and intersections

delta_time = 1
inter1 = Intersection()
inter2 = Intersection()
inter3 = Intersection()
#   #---\
#   |    #------------#(4)
#   #--/
inter4 = Intersection()
road1 = Road(dt=delta_time, start=inter1, end=inter2, num_cars=20, speed_limit=100, length=100, lanes=1, name="1")
road2 = Road(dt=delta_time, start=inter2, end=inter3, num_cars=20, speed_limit=100, length=100, lanes=1, name="2")
road3 = Road(dt=delta_time, start=inter3, end=inter1, num_cars=20, speed_limit=100, length=100, lanes=1, name="3")
road4 = Road(dt=delta_time, start=inter2, end=inter4, num_cars=20, speed_limit=100, length=100, lanes=1, name="4")
road5 = Road(dt=delta_time, start=inter2, end=inter4, num_cars=20, speed_limit=100, length=100, lanes=1, name="5")
street_map = Map(intersections = [inter1, inter2, inter3, inter4], roads=[road1, road2, road3, road4, road5])


In [28]:
# Create initial Networkx graph

G = nx.DiGraph()
G.add_nodes_from([1,2,3,"ralphs"])
G.add_edge(1, 2, dt=delta_time, num_cars=20, speed_limit=100, length=100, lanes=1, name="1")
G.add_edge(2, 3, dt=delta_time, num_cars=20, speed_limit=100, length=100, lanes=1, name="2")
G.add_edge(3, 1, dt=delta_time, num_cars=20, speed_limit=100, length=100, lanes=1, name="3")
G.add_edge(2, "ralphs", dt=delta_time, num_cars=20, speed_limit=100, length=100, lanes=1, name="4")
G.add_edge(2, "ralphs", dt=delta_time, num_cars=20, speed_limit=100, length=100, lanes=1, name="5")

# Draw the graph with edge colors
pos = {
    1: (0, 0),
    2: (1, 1),
    3: (2, 0),
    'ralphs': (3, 1),
}

norm = plt.Normalize(0, 1)  # Normalize to [0,25]
node_colors = [cm.YlOrRd(norm(0)), cm.YlOrRd(norm(0)), cm.YlOrRd(norm(0)), cm.YlOrRd(norm(0.7))]

In [51]:
(1,2) in G.edges
G[1][2]
G.out_degree(G.nodes)
G.nodes['ralphs']['test'] = 2
G.nodes['ralphs']
list(nx.all_simple_edge_paths(G, 1, 'ralphs'))
G[1][2]
for node in G.nodes:
    print(node)

1
2
3
ralphs


In [62]:
probabilities = [0.1, 0.3, 0.6, 0.000000000001]
random_index = [np.random.choice(len(probabilities), p=probabilities) for _ in range(5)]
random_index

[1, 2, 2, 2, 2]

In [26]:
# Define update function for one time step

def update(frame):
    ax.clear()  # Clear previous frame
    
    # Update traffic by one time step
    street_map.update()
    
    # Get relevant graph parameters, i.e. num_cars, terminations at ralphs
    num_cars_per_road = [road.num_cars for road in street_map.roads]
    num_terminations = [intersection.terminations for intersection in street_map.intersections]
    
    # Update graph parameters
    G[1][2]["num_cars"] = num_cars_per_road[0]
    G[2][3]["num_cars"] = num_cars_per_road[1]
    G[3][1]["num_cars"] = num_cars_per_road[2]
    G[2]['ralphs']["num_cars"] = num_cars_per_road[3]
    
    G.nodes['ralphs']['terminations'] = num_terminations[3]
    
    # Update edge_colors
    num_cars = nx.get_edge_attributes(G, 'num_cars')
    # Convert weights to a list and normalize them for color mapping
    num_cars_values = list(num_cars.values())
    norm = plt.Normalize(0, 25)  # Normalize to [0,25]
    edge_colors = [cm.YlOrRd(norm(num_cars[edge])) for edge in G.edges]

    # Redraw graph
    nx.draw(G, pos, ax=ax, with_labels=True, 
            node_color=node_colors, node_size=500, 
            edge_color=edge_colors, width=4)
    
    # Create labels for terminations, num_cars
    shift_down_pos = {node: (x, y - 0.05) for node, (x, y) in pos.items()}
    
    ralphs_terminations = {'ralphs': "Terminations:\n" + str(round(G.nodes['ralphs']["terminations"],2))}
    nx.draw_networkx_labels(G, shift_down_pos, ax=ax, labels=ralphs_terminations, font_size=8, font_color="black")
    
    road_num_cars = {edge: "Car Density: " + str(round(G[edge[0]][edge[1]]["num_cars"],2)) for edge in G.edges}
    nx.draw_networkx_edge_labels(G, shift_down_pos, ax=ax, edge_labels=road_num_cars, font_size=8, font_color="black")




In [27]:
# Create animation
fig, ax = plt.subplots()
ani = FuncAnimation(fig, update, frames=200, interval=200)
plt.close()
HTML(ani.to_jshtml())